# Interactive Plot

Load and listen to Data:

In [1]:
import parselmouth
from scipy import signal
import matplotlib.pyplot as plt
import ipywidgets as widgets
from ipywidgets import interact,interactive, interact_manual, Layout
import librosa
import IPython.display as ipd
import numpy as np
from bokeh.plotting import figure, output_file, show
from bokeh.io import push_notebook, output_notebook
from bokeh.layouts import gridplot
from bokeh.models import ColorBar, LogColorMapper, LogTicker, Slider, CustomJS

audio1, fs = librosa.load('a_8000.wav',sr=8000)
print("f_s =", fs)
ipd.Audio('a_8000.wav') # show audio player

f_s = 8000


## 2.) Frequency-Domain-Analysis: Spectrogram

In [2]:

window='hann'
windowlength = 2048
overlap = windowlength-1

fVec, tVec, spectroData = signal.spectrogram(audio1, fs, window=window, nperseg=windowlength, noverlap=overlap)
frameVec = np.array(range(0, len(tVec)-1))

index = (np.abs(fVec - 1500)).argmin()
spectroData = np.delete(spectroData, range(index, len(spectroData)), 0)
fVec = np.delete(fVec, range(index, len(fVec)))


spectroData = np.divide(spectroData, np.max(spectroData))

In [3]:

timeWidget = widgets.FloatSlider(min=tVec[0], max=tVec[-1], step=tVec[1]-tVec[0], value=tVec[0], description="Time in s")
#timeSlider = Slider(start=tVec[0], end=tVec[-1], value=tVec[0], step=tVec[1]-tVec[0], title="Time in s")
timeInStft = timeWidget.value
stftFrame = (np.abs(tVec - timeInStft)).argmin()

output_notebook()
p1 = figure(title="Spetrogram of Sound Sample",plot_width=600, plot_height=300, x_range=(tVec[0],tVec[-1]), y_range=(fVec[0],fVec[-1]))
p1.xaxis.axis_label = 'Time in s'
p1.yaxis.axis_label = 'Frequency in Hz'
color_mapper = LogColorMapper(palette="Viridis256", low=1e-3, high=1)
p1.image(image=[spectroData+np.abs(np.min(spectroData))], x=tVec[0], y=fVec[0], dw=tVec[-1], dh=fVec[-1], color_mapper=color_mapper)
p1.grid.visible=False
spectrumLine = p1.line([timeInStft, timeInStft], [fVec[0], fVec[-1]], line_width = 2, color = 'red')

p2 = figure(title="Spectrum of Selected STFT Frame",plot_width=600, plot_height=200, x_range=(fVec[0],fVec[-1]), y_range=(np.min(20*np.log10(spectroData[:,stftFrame])),0))
p2.xaxis.axis_label = 'Frequency in Hz'
p2.yaxis.axis_label = 'relative Magnitude in dB'
spectrumPlot = p2.line(fVec, np.log10(spectroData[:,stftFrame])*20, line_width = 2, color = 'red')

pAll = gridplot([[p2],[p1]])

def update_plot(timeInStft):
    stftFrame = (np.abs(tVec - timeInStft)).argmin()
    spectrumLine.data_source.data['x'] = [timeInStft, timeInStft]
    spectrumPlot.data_source.data['y'] = 20*np.log10(spectroData[:,stftFrame])
    push_notebook()
    
layout=Layout(width='100%')

w=interactive(update_plot,timeInStft=(tVec[0],tVec[-1],tVec[1]-tVec[0]),width='10px')
w.children[0].value=tVec[0]
w.children[0].layout=layout
w.children[0].description='time:'
show(pAll,notebook_handle=True)
display(w)


    

    

#show(timeSlider,notebook_handle=True)
#timeWidget.observe(on_value_change,names='value')
#timeSlider.on_change('value',on_value_change_Bokeh)
#print(timeSlider.on_change('value',Sliderchange))
#widgets.HBox([w],layout=Layout(width='1000px'))


Loading BokehJS ...

interactive(children=(FloatSlider(value=0.128, description='time:', layout=Layout(width='100%'), max=0.58325, …